# GOSTNets Example Notebook

### This phase analyzed the effect of disrupted roads on the mobility between cities. Travel times and flows were modeled for travel between major cities in Loas. We used the gravity model to estimate trip patterns. The ‘gravity’ assumption is that more trips occur between large cities close to each other.

- downloaded OSM pbf from ProtoMaps
- only using major road classes
- advanced snapping
- origins were created from calculated urban extent centroids using GHS data and GHS urban definitions
- for disruption analysis, eliminated from consideration the nearest road from each origin due to it creating too many failed routes
    - additional explanation: why were there failed routes? Because often when the road that was part of an origin or destination was removed, then no other route existed to reach the destination. 
- some failed routes still exist, so this is to be taken into consideration

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import sys, os, inspect, logging, importlib

import geopandas as gpd
import pandas as pd
import numpy as np
import osmnx as ox
import networkx as nx
from shapely.ops import split, unary_union
from shapely.geometry import box, Point

import matplotlib.pyplot as plt
import math

In [3]:
import pickle

In [4]:
# Get reference to GOSTNets
sys.path.append(r'../../../../GOSTnets')
import GOSTnets as gn

In [5]:
from GOSTnets.load_osm import *

## Load custom road data from shapefile
#### filtered out minor roads (residential, track, and unclassified, etc...) manually in QGIS before imported

In [6]:
import time
start_time = time.time()

In [7]:
f = r"input/LAO_fluvial_historical_retained4.shp"

In [8]:
# create OSM_to_network object from the load_osm GOSTnets sub-module
laos = OSM_to_network(f)

#### GOSTnets can read in a shapefile, but unlike an OSM.pbf it doesn't parse it, instead it imports it using GeoPandas
You need to rename the highway columns to 'infra_type' because that is what the generateRoadsGDF method expects

In [9]:
laos.roads_raw[:2]

fid    osm_id   highway  feature_le is_divided  tonnes_NOx  tonnes_N_1   
0  18.0  10639496  tertiary    0.132082      false    0.044336    0.335669  \
1  31.0  10640794  tertiary    0.044792      false    0.015035    0.335667   

   cars_per_d  hgv_per_da   tonnes_per       GDP  primary_gd  secondary_   
0  411.413668  109.602832  2323.580058  0.036449    0.006272     0.01268  \
1  411.411096  109.602147  2323.565531  0.012361    0.002127     0.00430   

   tertiary_g  vehicles_p  retain   
0    0.017496  521.016501       1  \
1    0.005933  521.013243       1   

                                            geometry  
0  LINESTRING (102.61857 17.95361, 102.61848 17.9...  
1  LINESTRING (102.61757 17.97053, 102.61785 17.9...

In [10]:
len(laos.roads_raw)

35407

In [11]:
laos.roads_raw = laos.roads_raw.rename(columns={"highway":"infra_type"})

In [12]:
shapely.__version__

'2.0.1'

In [13]:
laos.generateRoadsGDF(verbose = False)

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

...

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:292: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if "Point" == inter.type:
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY

/Users/tomgertin/opt/anaconda3/envs/geo_env/lib/python3.11/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/load_osm.py:228: ShapelyDeprecationWarning: The 'GeometryType()' method is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if line.geometryType() == 'MultiLineString':


In [14]:
laos.initialReadIn()

In [15]:
print(f"sec elapsed: {time.time() - start_time}")

sec elapsed: 61.39291763305664


In [16]:
UTMZ = 'epsg:32648'

WGS = 'epsg:4326' # do not adjust. OSM natively comes in ESPG 4326

In [17]:
# length starts off in km
gn.example_edge(laos.network)

(0, 33451, {'Wkt': <LINESTRING (101.182 17.507, 101.182 17.508)>, 'id': 19858, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '391852800', 'key': 'edge_19858', 'length': 0.053305821631184566})


In [18]:
# 1st test
#G_adv_w_time_gdf = gn.edge_gdf_from_graph(laos.network, geometry_tag='geometry')
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf.to_file("laos_rds_1st_test3.shp")

## Simplify graph step

In [19]:
%%time
# Topologically simplifies an input graph object by collapsing junctions and removing interstital nodes
# Squeezes clusters of nodes down to a single node if they are within the snapping tolerance
G_simplified = gn.simplify_junctions(laos.network, UTMZ, in_crs = {'init': 'epsg:4326'}, thresh = 10, verbose = True)

/Users/tomgertin/opt/anaconda3/envs/geo_env/lib/python3.11/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/Users/tomgertin/repos/valhalla_GOST_PublicGoods/Implementations/FY22/ACC_laos_criticality/../../../../GOSTnets/GOSTnets/core.py:1584: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  juncs_gdf_unproj['centroid'] = juncs_gdf_unproj.centroid
/Users/tomgertin/opt/anaconda3/envs/geo_env/lib/python3.11/site-packages/IPython/core/magics/execution.py:1325: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. 

Processing 0 of 37036
seconds elapsed: 0.030489206314086914
Processing 10000 of 37036
seconds elapsed: 0.11634302139282227
Processing 20000 of 37036
seconds elapsed: 0.20159196853637695
Processing 30000 of 37036
seconds elapsed: 0.28748011589050293
37036
CPU times: user 12.8 s, sys: 379 ms, total: 13.2 s
Wall time: 13.2 s


In [20]:
gn.example_edge(G_simplified,4)

(0, 33451, {'Wkt': <LINESTRING (101.182 17.507, 101.182 17.508)>, 'id': 19858, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '391852800', 'key': 'edge_19858', 'length': 0.053305821631184566, 'Type': 'legitimate'})
(1, 35218, {'Wkt': <LINESTRING (102.727 18.023, 102.725 18.019)>, 'id': 9214, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9214', 'length': 0.5020331388332742, 'Type': 'legitimate'})
(2, 27928, {'Wkt': <LINESTRING (101.417 20.485, 101.417 20.485, 101.417 20.485, 101.417 20.485)>, 'id': 29070, 'infra_type': 'tertiary', 'one_way': None, 'osm_id': '572689549', 'key': 'edge_29070', 'length': 0.05520916659081486, 'Type': 'legitimate'})
(3, 15427, {'Wkt': <LINESTRING (101.008 17.525, 101.008 17.525, 101.008 17.525)>, 'id': 15870, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '318392792', 'key': 'edge_15870', 'length': 0.03069976422181405, 'Type': 'legitimate'})


## Get rid of edges that have 0 length

In [21]:
# https://stackoverflow.com/questions/48094844/how-to-iterate-and-delete-specific-edges-in-networkx-directed-graph
thingsToChange = []
for edge in G_simplified.edges():
    length = G_simplified.get_edge_data(edge[0], edge[1])[0]['length']
    if length == 0:
       print('edge has 0 length')
       thingsToChange.append(edge)

edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length
edge has 0 length


In [22]:
for edge in thingsToChange:
    G_simplified.remove_edge(edge[0], edge[1])

## Add reflected edges (traffic goes in both directions)
The reason why we are adding reflected edges is because the next step is to use the GOSTnets custom_simplify function to remove  all nodes that are not intersections or dead-ends. This function will not work completly if the edges are not reflected.

In [23]:
#%%time
G_full = gn.add_missing_reflected_edges(G_simplified, verbose=True)

Processing 0 of 37027
seconds elapsed: 0.00011587142944335938
Processing 10000 of 37027
seconds elapsed: 0.006733894348144531
Processing 20000 of 37027
seconds elapsed: 0.01276397705078125
Processing 30000 of 37027
seconds elapsed: 0.01849079132080078
completed processing 74054 edges


In [24]:
# for testing
#G_adv_w_time_gdf_G_full = gn.edge_gdf_from_graph(G_full, geometry_tag='Wkt')
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf_G_full.to_file("G_adv_laos_major_rds_undirected_largest4.shp")

In [25]:
# for testing
#G_adv_w_time_gdf_G_full_nodes = gn.node_gdf_from_graph(G_full)
#G_adv_w_time_gdf_G_full_nodes = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf_G_full_nodes.to_file("G_adv_laos_major_rds_undirected_largest4_nodes.shp")

## Additional simplify step using GOSTnets custom_simplify function to remove all nodes that are not intersections or dead-ends

In [26]:
%%time
G_full_simplify_step2 = gn.custom_simplify(G_full)

CPU times: user 1.9 s, sys: 19.2 ms, total: 1.92 s
Wall time: 1.92 s


In [27]:
gn.example_edge(G_full_simplify_step2,4)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 0.016002568065588845, 'Type': 'legitimate'})
(1, 35427, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9230, 'infra_type': 'primary_link', 'one_way': None, 'osm_id': '221460953', 'key': 'edge_9230', 'length': 0.012132278961277224, 'Type': 'legitimate'})
(1, 16050, {'Wkt': [<LINESTRING (102.727 18.023, 102.725 18.019)>, <LINESTRING (102.725 18.019, 102.724 18.017)>, <LINESTRING (102.724 18.017, 102.724 18.016, 102.724 18.015, 102.722 18.01)>], 'id': 9214, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'length': 1.5184586030002702, 'Type': 'legitimate', 'geometry': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>})
(4, 28024, {'Wkt': <LINESTRING (102.589 17.989, 102.589 17.989)>, 'id': 4545, 'infra_type': 'tertiary', 'one_way': None, 'osm_id': '102994623', 'k

In [28]:
# unify geometry, this is done because during the custom_simplify function if Wkt geometries are merged then they will get stored 
# in the 'geometry' key; but the edges that are not merged will only get a Wkt key
count=0
for u,v,e in G_full_simplify_step2.edges(data=True):
    count+=1
    #if count < 100:
    if 'geometry' in e.keys():
        e['Wkt'] = e['geometry']

In [29]:
gn.example_edge(G_full_simplify_step2,4)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 0.016002568065588845, 'Type': 'legitimate'})
(1, 35427, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9230, 'infra_type': 'primary_link', 'one_way': None, 'osm_id': '221460953', 'key': 'edge_9230', 'length': 0.012132278961277224, 'Type': 'legitimate'})
(1, 16050, {'Wkt': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>, 'id': 9214, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'length': 1.5184586030002702, 'Type': 'legitimate', 'geometry': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>})
(4, 28024, {'Wkt': <LINESTRING (102.589 17.989, 102.589 17.989)>, 'id': 4545, 'infra_type': 'tertiary', 'one_way': None, 'osm_id': '102994623', 'key': 'edge_4545', 'length': 0.016212538410478927, 'Type': 'legitimate'})


In [30]:
# 2nd test
#G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_full_simplify_step2, geometry_tag='Wkt')

In [31]:
#G_adv_w_time_gdf

In [32]:
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['geometry'])
#G_adv_w_time_gdf.to_file("laos_rds_2nd_test3.shp")

## now get the largest sub-graph

In [33]:
# Identify only the largest graph

# compatible with NetworkX 2.4
list_of_subgraphs = list(G_full_simplify_step2.subgraph(c).copy() for c in nx.strongly_connected_components(G_full_simplify_step2))
max_graph = None
max_edges = 0
for i in list_of_subgraphs:
    if i.number_of_edges() > max_edges:
        max_edges = i.number_of_edges()
        max_graph = i

# set your graph equal to the largest sub-graph
G_largest = max_graph

In [34]:
G_largest

In [35]:
#largest = max(nx.strongly_connected_components(G_full_simplify_step2), key=len)

In [36]:
#largest

In [37]:
# for testing
#G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_largest, geometry_tag='Wkt')
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf.to_file("G_adv_laos_major_rds_undirected_largest5.shp")

## In another notebook I calculated urban extent centroids using GHS data and GHS urban definitions. 

In [38]:
#origins = gpd.read_file(r'input/laos_urban_extents_worldpop/laos_urban_extents_worldpop.shp')
origins = gpd.read_file(r'input/laos_urban_clusters_GHS_pop_yr2022_200dense_pts.shp')

In [39]:
origins['osmid'] = 1110000000 + origins.index
origins

ID           Pop                    geometry       osmid
0     5157  14214.519489  POINT (101.14740 21.18301)  1110000000
1     5930  38589.649943  POINT (101.40998 20.96925)  1110000001
2     6063   5026.444239  POINT (101.75870 20.91135)  1110000002
3     7017  46434.021615  POINT (101.98812 20.68555)  1110000003
4     7197  10209.088599  POINT (102.45826 20.62369)  1110000004
..     ...           ...                         ...         ...
118  38687   5501.743691  POINT (105.77835 14.13601)  1110000118
119  38765   5609.059167  POINT (105.79669 14.08817)  1110000119
120  38796   5030.252792  POINT (105.86173 14.10705)  1110000120
121  39013   7557.503249  POINT (105.88487 14.05850)  1110000121
122  39308   8021.070721  POINT (105.93184 13.99032)  1110000122

[123 rows x 4 columns]

## Snap the urban extent centroids to the graph: use advanced snapping

In [40]:
G_utm = gn.utm_of_graph(G_largest)
G_utm

'+proj=utm +zone=48 +ellps=WGS84 +datum=WGS84 +units=m +no_defs'

### Note: make sure the input graph is in meters, so that the output will consistently be in meters

In [41]:
for u, v, data in G_largest.edges(data=True):

    orig_len = data['length'] * 1000

    # Note that this is a MultiDiGraph so there could
    # be multiple indices here, I naively assume this is not
    # the case
    #actually saves the length in meters
    data['length'] = orig_len

In [42]:
snapped_origins_df = gn.pandana_snap_c(G_largest, origins, source_crs='epsg:4326', target_crs=G_utm)

In [43]:
snapped_origins_df

ID           Pop                    geometry       osmid     NN   
0     5157  14214.519489  POINT (101.14740 21.18301)  1110000000  31313  \
1     5930  38589.649943  POINT (101.40998 20.96925)  1110000001   4935   
2     6063   5026.444239  POINT (101.75870 20.91135)  1110000002   8705   
3     7017  46434.021615  POINT (101.98812 20.68555)  1110000003   6433   
4     7197  10209.088599  POINT (102.45826 20.62369)  1110000004  35086   
..     ...           ...                         ...         ...    ...   
118  38687   5501.743691  POINT (105.77835 14.13601)  1110000118   7732   
119  38765   5609.059167  POINT (105.79669 14.08817)  1110000119  15055   
120  38796   5030.252792  POINT (105.86173 14.10705)  1110000120  27659   
121  39013   7557.503249  POINT (105.88487 14.05850)  1110000121  30945   
122  39308   8021.070721  POINT (105.93184 13.99032)  1110000122  16080   

         NN_dist  
0     232.266227  
1    2688.572853  
2     618.851276  
3      32.995339  
4      82.189010  
..           ...  
118  3833.747111  
119  1045.780916  
120  2955.091508  
121  2509.788964  
122  1771.490154  

[123 rows x 6 columns]

In [44]:
originNodes = list(snapped_origins_df['NN'].unique())

In [45]:
len(originNodes)

123

## Check if more than one origins are snapped to the same nearest node, if so then make manual edits to the origin shapefile

In [46]:
snapped_origins_df[snapped_origins_df.duplicated(subset=['NN'])]

Empty GeoDataFrame
Columns: [ID, Pop, geometry, osmid, NN, NN_dist]
Index: []

In [47]:
#snapped_origins_df[snapped_origins_df.duplicated(subset=['NN'])]

In [48]:
#G_full_simplified_undirected_largest_2, pois_meter, new_footway_edges = gn.advanced_snap(G_largest, origins, u_tag = 'stnode', v_tag = 'endnode', node_key_col='osmid', edge_key_col='osmid', poi_key_col='osmid', road_col = 'infra_type', threshold=20000, measure_crs=G_utm, verbose = True)

In [49]:
#pois_meter[:3]

## Add time to the edges based on default speeds

In [50]:
# 3rd test
#G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_full_simplified_undirected_largest_2, geometry_tag='geometry')
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf.to_file("laos_rds_3rd_test.shp")

In [51]:
# note that the length above is in meters
G_w_time = gn.convert_network_to_time(G_largest, 'length', road_col = 'infra_type')

In [52]:
# Also note that due to convert_network_to_time the lengths are not in meters
gn.example_edge(G_w_time, 3)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 16.002568065588846, 'Type': 'legitimate', 'time': 1.440231125902996, 'mode': 'drive'})
(1, 35427, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9230, 'infra_type': 'primary_link', 'one_way': None, 'osm_id': '221460953', 'key': 'edge_9230', 'length': 12.132278961277224, 'Type': 'legitimate', 'time': 1.2478915503028003, 'mode': 'drive'})
(1, 16050, {'Wkt': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>, 'id': 9214, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'length': 1518.4586030002702, 'Type': 'legitimate', 'geometry': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>, 'time': 136.66127427002434, 'mode': 'drive'})


In [53]:
# for testing
#G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_w_time, geometry_tag='geometry')
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf.to_file("phase1_G_adv_w_time_laos_major_rds.shp")

In [54]:
# for testing
#G_adv_w_time_gdf = gn.node_gdf_from_graph(G_w_time, geometry_tag='geometry')
#G_adv_w_time_gdf.to_file("G_adv_w_time_laos_major_rds_nodes.shp")
#G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
#G_adv_w_time_gdf.to_file("G_adv_w_time_laos_major_rds.shp")

In [55]:
len(originNodes)

123

# Calculate OD Matrix and baseline

In [56]:
%%time
OD_matrix = gn.calculate_OD(G_w_time, originNodes, originNodes, fail_value=-1, weight='time', one_way_roads_exist = True)

CPU times: user 673 ms, sys: 1.66 ms, total: 675 ms
Wall time: 674 ms


In [57]:
OD_matrix_df = pd.DataFrame(OD_matrix, index=originNodes, columns=originNodes)

In [58]:
OD_matrix_df

31313          4935           8705           6433    
31313       0.000000    7611.978424   12706.047649   17284.788825  \
4935     7611.978424       0.000000    5912.125233   10490.866408   
8705    12706.047649    5912.125233       0.000000    4578.741175   
6433    17284.788825   10490.866408    4578.741175       0.000000   
35086   25552.482018   18758.559601   12846.434369    8268.655961   
...              ...            ...            ...            ...   
7732   132130.209688  125336.287271  119424.162038  114846.383631   
15055  131794.713251  125000.790835  119088.665602  114510.887194   
27659  130770.229835  123976.307418  118064.182185  113486.403778   
30945  131464.849283  124670.926867  118758.801634  114181.023226   
16080  132075.918570  125281.996154  119369.870921  114792.092513   

               35086          22045          12557          28219   
31313   25552.482018   21297.096074   26220.338247   65950.681108  \
4935    18758.559601   14503.173657   19426.415831   59156.758691   
8705    12846.434369    8591.048424   13514.290598   53244.633458   
6433     8268.655961    4012.402169    8936.512190   48666.855051   
35086       0.000000   12235.619976    2566.043918   40398.199090   
...              ...            ...            ...            ...   
7732   108475.915359  118813.347646  105909.871440  114099.183325   
15055  108140.418922  118477.851210  105574.375004  113763.686889   
27659  107115.935506  117453.367793  104549.891587  112739.203472   
30945  107810.554954  118147.987242  105244.511036  113433.822921   
16080  108421.624241  118759.056529  105855.580323  114044.892208   

               11728          27665  ...          1962           26726   
31313   25426.995703   22729.446041  ...  134326.513373  135552.798176  \
4935    18215.891101   15117.467618  ...  127532.590956  128758.875759   
8705    12720.948053   20617.976122  ...  121620.465723  122846.750526   
6433     8143.169646   25196.717297  ...  117042.687316  118268.972119   
35086   15503.015758   33464.410491  ...  110672.219044  111898.503847   
...              ...            ...  ...            ...            ...   
7732   120713.970161  132243.345754  ...   28281.662350   29507.947153   
15055  120378.473725  131907.849318  ...   27946.165913   29172.450716   
27659  119353.990308  130883.365901  ...   26921.682497   28147.967300   
30945  120048.609757  131577.985350  ...   27616.301945   28842.586748   
16080  120659.679044  132189.054637  ...   28227.371232   29453.656035   

               6385           7971           20108          7732    
31313  126688.776584  128534.437502  136336.119660  132130.209688  \
4935   119894.854167  121740.515085  129542.197243  125336.287271   
8705   113982.728934  115828.389852  123630.072010  119424.162038   
6433   109404.950527  111250.611445  119052.293603  114846.383631   
35086  103034.482255  104880.143173  112681.825331  108475.915359   
...              ...            ...            ...            ...   
7732    20455.625065   22301.285983   30102.968141       0.000000   
15055   20120.128628   21965.789547   29767.471705     354.829907   
27659   19095.645212   20941.306130   28742.988288    1359.979853   
30945   19790.264660   21635.925579   29437.607737    2054.599301   
16080   20401.333947   22246.994866   30048.677024    2682.389132   

               15055          27659          30945          16080  
31313  131794.713251  130770.229835  131464.849283  132075.918570  
4935   125000.790835  123976.307418  124670.926867  125281.996154  
8705   119088.665602  118064.182185  118758.801634  119369.870921  
6433   114510.887194  113486.403778  114181.023226  114792.092513  
35086  108140.418922  107115.935506  107810.554954  108421.624241  
...              ...            ...            ...            ...  
7732      354.829907    1359.979853    2054.599301    2682.389132  
15055       0.000000    1024.483417    1719.102865    2346.892696  
27659    1024.483417       

In [59]:
OD_matrix_df_min = OD_matrix_df / 60

In [60]:
OD_matrix_df_min

31313        4935         8705         6433         35086   
31313     0.000000   126.866307   211.767461   288.079814   425.874700  \
4935    126.866307     0.000000    98.535421   174.847773   312.642660   
8705    211.767461    98.535421     0.000000    76.312353   214.107239   
6433    288.079814   174.847773    76.312353     0.000000   137.810933   
35086   425.874700   312.642660   214.107239   137.810933     0.000000   
...            ...          ...          ...          ...          ...   
7732   2202.170161  2088.938121  1990.402701  1914.106394  1807.931923   
15055  2196.578554  2083.346514  1984.811093  1908.514787  1802.340315   
27659  2179.503831  2066.271790  1967.736370  1891.440063  1785.265592   
30945  2191.080821  2077.848781  1979.313361  1903.017054  1796.842583   
16080  2201.265310  2088.033269  1989.497849  1913.201542  1807.027071   

             22045        12557        28219        11728        27665  ...   
31313   354.951601   437.005637  1099.178018   423.783262   378.824101  ...  \
4935    241.719561   323.773597   985.945978   303.598185   251.957794  ...   
8705    143.184140   225.238177   887.410558   212.015801   343.632935  ...   
6433     66.873369   148.941870   811.114251   135.719494   419.945288  ...   
35086   203.927000    42.767399   673.303318   258.383596   557.740175  ...   
...            ...          ...          ...          ...          ...  ...   
7732   1980.222461  1765.164524  1901.653055  2011.899503  2204.055763  ...   
15055  1974.630853  1759.572917  1896.061448  2006.307895  2198.464155  ...   
27659  1957.556130  1742.498193  1878.986725  1989.233172  2181.389432  ...   
30945  1969.133121  1754.075184  1890.563715  2000.810163  2192.966422  ...   
16080  1979.317609  1764.259672  1900.748203  2010.994651  2203.150911  ...   

             1962         26726        6385         7971         20108   
31313  2238.775223  2259.213303  2111.479610  2142.240625  2272.268661  \
4935   2125.543183  2145.981263  1998.247569  2029.008585  2159.036621   
8705   2027.007762  2047.445842  1899.712149  1930.473164  2060.501200   
6433   1950.711455  1971.149535  1823.415842  1854.176857  1984.204893   
35086  1844.536984  1864.975064  1717.241371  1748.002386  1878.030422   
...            ...          ...          ...          ...          ...   
7732    471.361039   491.799119   340.927084   371.688100   501.716136   
15055   465.769432   486.207512   335.335477   366.096492   496.124528   
27659   448.694708   469.132788   318.260754   349.021769   479.049805   
30945   460.271699   480.709779   329.837744   360.598760   490.626796   
16080   470.456187   490.894267   340.022232   370.783248   500.811284   

             7732         15055        27659        30945        16080  
31313  2202.170161  2196.578554  2179.503831  2191.080821  2201.265310  
4935   2088.938121  2083.346514  2066.271790  2077.848781  2088.033269  
8705   1990.402701  1984.811093  1967.736370  1979.313361  1989.497849  
6433   1914.106394  1908.514787  1891.440063  1903.017054  1913.201542  
35086  1807.931923  1802.340315  1785.265592  1796.842583  1807.027071  
...            ...          ...          ...          ...          ...  
7732      0.000000     5.913832    22.666331    34.243322    44.706486  
15055     5.913832     0.000000    17.074724    28.651714    39.114878  
27659    22.666331    17.074724     0.000000    11.576991    22.040155  
30945    34.243322    28.651714    11.576991     0.000000    33.617145  
16080    44.706486    39.114878    22.040155    33.617145     0.000000  

[123 rows x 123 columns]

In [61]:
type(OD_matrix_df_min)

pandas.core.frame.DataFrame

# Main Algorithm to calculate flows

In [62]:
def calculate_flows(od, oWeight=[], dWeight=[], decayVal=0.0003850818):            
    ''' 
    New function writted to calculate flows
         decayVals=[0.01,
         0.005,
         0.001,
         0.0007701635,   # Market access halves every 15 mins
         0.0003850818,   # Market access halves every 30 mins
         0.0001925409,   # Market access halves every 60 mins
         0.0000962704,   # Market access halves every 120 mins
         0.0000385082,   # Market access halves every 300 mins
         0.00001]):
    decay values assume the OD matrix values are in seconds
    '''     
    
    # if weights don't exist, then make the weights equal 1
    if len(oWeight) != od.shape[0]:
        print('oWeight')
        oWeight = [1] * od.shape[0]
    if len(dWeight) != od.shape[1]:
        dWeight = [1] * od.shape[1]
    allRes = []
    allRes_flows = []

    outOD = od * 0
    allRes = []

    # decay Function returns a value between 0-1. The greater the travel time, the smaller the distance decay value.
    #decayFunction = lambda x: np.exp(-1 * decayVal * x)
    
    # include a postive lambda so that the greater the travel time, the greater the distance decay value.
    decayFunction = lambda x: np.exp(decayVal * x)
   
    for row in range(0, od.shape[0]):
        curRow = od[row,:]
        print('print curRow')
        print(curRow)
        
        #curRow_flows = od[row,:]
        decayedRow = decayFunction(curRow)
        decayedRowVal = decayedRow * curRow
        #print('print decayedRow')
        #print(type(decayedRow))
        #print(decayedRow)
        
        decayedRowVal_inv = np.divide(1, decayedRowVal, out=np.zeros_like(decayedRowVal), where=decayedRowVal!=0)
       
        # if travel time is very large, then the decayed value may be zero, in this case replace all zeros with 1s
        #decayedRow[decayedRow < 1] = 1
       
        #decayedRow_sum = sum(decayedRow)

        #print('print decayedRow/decayedRow_sum')
        #print(decayedRow/decayedRow_sum)
        #print(type(decayedRow/decayedRow_sum))
       
        #print('print population allocations')
        #print(test_weights[row]*(decayedRow/decayedRow_sum))
        
        gravity_model = (oWeight*decayedRowVal_inv)/sum(oWeight*decayedRowVal_inv)
        # estimated flow
        outOD[row,:] = oWeight[row] * gravity_model
        
        #print('check that sum of flow equals pop')
        #print(sum(oWeight[row] * (gravity_model)))
        
       
        #outOD[row,:] = oWeight[row] * decayedRow * (dWeight[row]/destinations_pop_sum)
        #outOD[row,:] = oWeight[row]*(decayedRow/decayedRow_sum)
        #outOD[row,:] = (decayedRow/decayedRow_sum)
        print('print outOD[row,:]')
        #print(oWeight[row]*(decayedRow/decayedRow_sum))
        allRes.append(outOD[row,:])

    return(allRes)

In [63]:
len(origins['Pop'].to_list())

123

In [64]:
origins

ID           Pop                    geometry       osmid
0     5157  14214.519489  POINT (101.14740 21.18301)  1110000000
1     5930  38589.649943  POINT (101.40998 20.96925)  1110000001
2     6063   5026.444239  POINT (101.75870 20.91135)  1110000002
3     7017  46434.021615  POINT (101.98812 20.68555)  1110000003
4     7197  10209.088599  POINT (102.45826 20.62369)  1110000004
..     ...           ...                         ...         ...
118  38687   5501.743691  POINT (105.77835 14.13601)  1110000118
119  38765   5609.059167  POINT (105.79669 14.08817)  1110000119
120  38796   5030.252792  POINT (105.86173 14.10705)  1110000120
121  39013   7557.503249  POINT (105.88487 14.05850)  1110000121
122  39308   8021.070721  POINT (105.93184 13.99032)  1110000122

[123 rows x 4 columns]

In [65]:
origins['Pop'].sum()

2189308.3370425887

In [66]:
OD_matrix.shape

(123, 123)

## Calculate flows

In [67]:
#OD_matrix_df_min.shape

In [68]:
#test
np.exp(-1 * 0.0001925409 * 3600)

0.4999999702799735

In [116]:
# 0.0007701635,   # Market access halves every 15 mins
# 0.0003850818,   # Market access halves every 30 mins
# 0.0001925409,   # Market access halves every 60 mins
# 0.0000962704,   # Market access halves every 120 mins
# 0.0000385082,   # Market access halves every 300 mins
access_city_flows = calculate_flows(OD_matrix, oWeight = origins['Pop'].to_list(), decayVal=0.0000385082)

print curRow
[     0.           7611.97842369  12706.04764937  17284.78882461
  25552.48201791  21297.0960737   26220.33824734  65950.68110782
  25426.9957028   22729.44604131  24939.81143445  25244.90437026
  25464.74556532  42533.74614181  26081.05518989  82698.75219938
  34509.51291725  38470.66422374  38368.90056977  61992.32831707
  61997.51659903  38752.39119937  35357.56965418  63485.00097936
  59952.30183805  39261.48012658  57312.7843213   44160.42957169
  45313.96330882  45007.64769597  46843.56836643  47614.07297756
  50485.64052092  66432.03507556  52612.18588925  75421.98384016
  77645.1798966   77402.18659221  56454.75879888  74345.31485675
  54845.96624324  56449.62668954  73405.83601935  61879.94201895
  56722.63196606  62067.93541731  58135.03788227  71978.64428195
  55693.42898544  63364.70286201  64349.55189659  56690.81363915
  58079.82168799  61134.07621099  88790.72554913  57771.56980517
  80015.82302822  62140.99698181  60011.26070483  57809.55769636
  60466.7066

In [117]:
access_city_flows

[array([0.00000000e+00, 5.31484493e+03, 3.40859183e+02, 1.94053923e+03,
        2.09911399e+02, 1.54409609e+02, 2.79167846e+02, 3.65402151e+01,
        1.37867188e+02, 1.25470740e+03, 1.52702174e+02, 1.19985176e+02,
        3.95705529e+02, 1.04270686e+02, 1.13425918e+02, 5.53625563e+00,
        8.50485064e+02, 7.23644735e+01, 4.19489553e+01, 1.08414795e+01,
        1.71742848e+01, 5.68317676e+01, 9.33616413e+01, 1.06401610e+01,
        1.20180959e+01, 6.14723280e+01, 1.32304197e+02, 1.90211441e+02,
        2.84426416e+01, 4.13651795e+01, 7.15508236e+01, 3.46920623e+01,
        3.74303737e+01, 1.66768407e+01, 2.30071220e+01, 8.37507972e+00,
        1.20205898e+01, 5.65627897e+00, 2.09411188e+01, 2.57850734e+01,
        2.59984005e+01, 4.47412294e+01, 1.72071441e+01, 2.09297021e+01,
        4.11280711e+01, 1.14916522e+01, 2.48555138e+01, 4.27003352e+01,
        6.37364928e+01, 3.96485052e+01, 2.32322572e+01, 2.48805860e+01,
        1.43043201e+01, 1.92002281e+01, 1.43282070e+01, 3.910649

In [118]:
flow_matrix_pd = pd.DataFrame(access_city_flows, columns = originNodes, index = originNodes)

In [119]:
flow_matrix_pd

31313        4935         8705         6433         35086   
31313     0.000000  5314.844928   340.859183  1940.539228   209.911399  \
4935   4141.314302     0.000000  2013.024101  8785.819342   785.736174   
8705    138.312439  1048.304911     0.000000  1714.549354    97.722843   
6433   1010.828596  5873.402547  2200.993922     0.000000  2147.565201   
35086    82.536275   396.495253    94.693178  1621.063788     0.000000   
...            ...          ...          ...          ...          ...   
7732      0.085839     0.319130     0.054779     0.627660     0.186723   
15055     0.083688     0.311179     0.053421     0.612172     0.182147   
27659     0.078368     0.291519     0.050067     0.573931     0.170859   
30945     0.148685     0.552932     0.094937     1.088030     0.323790   
16080     0.186938     0.695012     0.119303     1.366994     0.406680   

             22045        12557       28219        11728        27665  ...   
31313   154.409609   279.167846   36.540215   137.867188  1254.707400  ...  \
4935    623.072791  1035.423760  111.942019   537.389997  5349.836022  ...   
8705     89.589709   126.771029   10.593126    64.497973   215.284228  ...   
6433   2713.419466  2711.738457  163.934088  1425.196180  1751.395226  ...   
35086   107.590908  2003.065974   45.063937    93.577415   159.177362  ...   
...            ...          ...         ...          ...          ...  ...   
7732      0.059586     0.295606    0.304329     0.068123     0.292499  ...   
15055     0.058110     0.288383    0.296825     0.066433     0.285171  ...   
27659     0.054463     0.270575    0.278299     0.062255     0.267039  ...   
30945     0.103270     0.512676    0.527565     0.118056     0.506649  ...   
16080     0.129771     0.643832    0.662805     0.148363     0.636999  ...   

           1962       26726       6385       7971       20108        7732    
31313   1.585564   0.577321    1.364333   0.881402   0.353855     0.361065  \
4935    4.589143   1.670150    3.961549   2.557204   1.023369     1.045966   
8705    0.409872   0.149098    0.354919   0.228922   0.091332     0.093499   
6433    6.024396   2.190620    5.230384   3.371345   1.341562     1.375252   
35086   1.351334   0.491085    1.177963   0.758500   0.300634     0.308823   
...          ...        ...         ...        ...        ...          ...   
7732   41.132930  14.485571   46.488308  27.948697   8.817089     0.000000   
15055  40.480949  14.248857   45.962547  27.594530   8.671035  1898.883849   
27659  39.043942  13.721097   44.996987  26.893603   8.343800   425.721612   
30945  72.597553  25.540731   82.812867  49.648819  15.539068   537.480469   
16080  89.714103  31.591625  101.469263  60.989728  19.228516   519.675277   

             15055        27659        30945       16080  
31313     0.373844     0.351489     0.511426    0.527720  
4935      1.083134     1.018801     1.481954    1.528783  
8705      0.096834     0.091120     0.132506    0.136660  
6433      1.424470     1.340878     1.949445    2.010146  
35086     0.319930     0.301316     0.437912    0.451406  
...            ...          ...          ...         ...  
7732   2016.603579   453.939569   439.516482  348.767036  
15055     0.000000   586.008513   510.832806  387.652260  
27659   583.651647     0.000000  1174.672068  639.223308  
30945   663.419809  1531.709856     0.000000  799.351985  
16080   613.424445  1015.597378   973.973547    0.000000  

[123 rows x 123 columns]

In [120]:
flow_matrix_pd

31313        4935         8705         6433         35086   
31313     0.000000  5314.844928   340.859183  1940.539228   209.911399  \
4935   4141.314302     0.000000  2013.024101  8785.819342   785.736174   
8705    138.312439  1048.304911     0.000000  1714.549354    97.722843   
6433   1010.828596  5873.402547  2200.993922     0.000000  2147.565201   
35086    82.536275   396.495253    94.693178  1621.063788     0.000000   
...            ...          ...          ...          ...          ...   
7732      0.085839     0.319130     0.054779     0.627660     0.186723   
15055     0.083688     0.311179     0.053421     0.612172     0.182147   
27659     0.078368     0.291519     0.050067     0.573931     0.170859   
30945     0.148685     0.552932     0.094937     1.088030     0.323790   
16080     0.186938     0.695012     0.119303     1.366994     0.406680   

             22045        12557       28219        11728        27665  ...   
31313   154.409609   279.167846   36.540215   137.867188  1254.707400  ...  \
4935    623.072791  1035.423760  111.942019   537.389997  5349.836022  ...   
8705     89.589709   126.771029   10.593126    64.497973   215.284228  ...   
6433   2713.419466  2711.738457  163.934088  1425.196180  1751.395226  ...   
35086   107.590908  2003.065974   45.063937    93.577415   159.177362  ...   
...            ...          ...         ...          ...          ...  ...   
7732      0.059586     0.295606    0.304329     0.068123     0.292499  ...   
15055     0.058110     0.288383    0.296825     0.066433     0.285171  ...   
27659     0.054463     0.270575    0.278299     0.062255     0.267039  ...   
30945     0.103270     0.512676    0.527565     0.118056     0.506649  ...   
16080     0.129771     0.643832    0.662805     0.148363     0.636999  ...   

           1962       26726       6385       7971       20108        7732    
31313   1.585564   0.577321    1.364333   0.881402   0.353855     0.361065  \
4935    4.589143   1.670150    3.961549   2.557204   1.023369     1.045966   
8705    0.409872   0.149098    0.354919   0.228922   0.091332     0.093499   
6433    6.024396   2.190620    5.230384   3.371345   1.341562     1.375252   
35086   1.351334   0.491085    1.177963   0.758500   0.300634     0.308823   
...          ...        ...         ...        ...        ...          ...   
7732   41.132930  14.485571   46.488308  27.948697   8.817089     0.000000   
15055  40.480949  14.248857   45.962547  27.594530   8.671035  1898.883849   
27659  39.043942  13.721097   44.996987  26.893603   8.343800   425.721612   
30945  72.597553  25.540731   82.812867  49.648819  15.539068   537.480469   
16080  89.714103  31.591625  101.469263  60.989728  19.228516   519.675277   

             15055        27659        30945       16080  
31313     0.373844     0.351489     0.511426    0.527720  
4935      1.083134     1.018801     1.481954    1.528783  
8705      0.096834     0.091120     0.132506    0.136660  
6433      1.424470     1.340878     1.949445    2.010146  
35086     0.319930     0.301316     0.437912    0.451406  
...            ...          ...          ...         ...  
7732   2016.603579   453.939569   439.516482  348.767036  
15055     0.000000   586.008513   510.832806  387.652260  
27659   583.651647     0.000000  1174.672068  639.223308  
30945   663.419809  1531.709856     0.000000  799.351985  
16080   613.424445  1015.597378   973.973547    0.000000  

[123 rows x 123 columns]

In [121]:
flow_matrix_pd.sum()

31313     8360.501756
4935     27184.757986
8705      6597.293100
6433     37096.620454
35086    10418.599529
             ...     
7732      4990.188473
15055     5568.028482
27659     5257.492171
30945     5448.147000
16080     4531.555266
Length: 123, dtype: float64

In [122]:
flow_matrix_pd.sum().sum()

2189308.3370425887

In [123]:
origins

ID           Pop                    geometry       osmid
0     5157  14214.519489  POINT (101.14740 21.18301)  1110000000
1     5930  38589.649943  POINT (101.40998 20.96925)  1110000001
2     6063   5026.444239  POINT (101.75870 20.91135)  1110000002
3     7017  46434.021615  POINT (101.98812 20.68555)  1110000003
4     7197  10209.088599  POINT (102.45826 20.62369)  1110000004
..     ...           ...                         ...         ...
118  38687   5501.743691  POINT (105.77835 14.13601)  1110000118
119  38765   5609.059167  POINT (105.79669 14.08817)  1110000119
120  38796   5030.252792  POINT (105.86173 14.10705)  1110000120
121  39013   7557.503249  POINT (105.88487 14.05850)  1110000121
122  39308   8021.070721  POINT (105.93184 13.99032)  1110000122

[123 rows x 4 columns]

In [124]:
origins['Pop'].sum()

2189308.3370425887

### test, is flow matrix symmetric? 

In [125]:
flow_matrix_pd

31313        4935         8705         6433         35086   
31313     0.000000  5314.844928   340.859183  1940.539228   209.911399  \
4935   4141.314302     0.000000  2013.024101  8785.819342   785.736174   
8705    138.312439  1048.304911     0.000000  1714.549354    97.722843   
6433   1010.828596  5873.402547  2200.993922     0.000000  2147.565201   
35086    82.536275   396.495253    94.693178  1621.063788     0.000000   
...            ...          ...          ...          ...          ...   
7732      0.085839     0.319130     0.054779     0.627660     0.186723   
15055     0.083688     0.311179     0.053421     0.612172     0.182147   
27659     0.078368     0.291519     0.050067     0.573931     0.170859   
30945     0.148685     0.552932     0.094937     1.088030     0.323790   
16080     0.186938     0.695012     0.119303     1.366994     0.406680   

             22045        12557       28219        11728        27665  ...   
31313   154.409609   279.167846   36.540215   137.867188  1254.707400  ...  \
4935    623.072791  1035.423760  111.942019   537.389997  5349.836022  ...   
8705     89.589709   126.771029   10.593126    64.497973   215.284228  ...   
6433   2713.419466  2711.738457  163.934088  1425.196180  1751.395226  ...   
35086   107.590908  2003.065974   45.063937    93.577415   159.177362  ...   
...            ...          ...         ...          ...          ...  ...   
7732      0.059586     0.295606    0.304329     0.068123     0.292499  ...   
15055     0.058110     0.288383    0.296825     0.066433     0.285171  ...   
27659     0.054463     0.270575    0.278299     0.062255     0.267039  ...   
30945     0.103270     0.512676    0.527565     0.118056     0.506649  ...   
16080     0.129771     0.643832    0.662805     0.148363     0.636999  ...   

           1962       26726       6385       7971       20108        7732    
31313   1.585564   0.577321    1.364333   0.881402   0.353855     0.361065  \
4935    4.589143   1.670150    3.961549   2.557204   1.023369     1.045966   
8705    0.409872   0.149098    0.354919   0.228922   0.091332     0.093499   
6433    6.024396   2.190620    5.230384   3.371345   1.341562     1.375252   
35086   1.351334   0.491085    1.177963   0.758500   0.300634     0.308823   
...          ...        ...         ...        ...        ...          ...   
7732   41.132930  14.485571   46.488308  27.948697   8.817089     0.000000   
15055  40.480949  14.248857   45.962547  27.594530   8.671035  1898.883849   
27659  39.043942  13.721097   44.996987  26.893603   8.343800   425.721612   
30945  72.597553  25.540731   82.812867  49.648819  15.539068   537.480469   
16080  89.714103  31.591625  101.469263  60.989728  19.228516   519.675277   

             15055        27659        30945       16080  
31313     0.373844     0.351489     0.511426    0.527720  
4935      1.083134     1.018801     1.481954    1.528783  
8705      0.096834     0.091120     0.132506    0.136660  
6433      1.424470     1.340878     1.949445    2.010146  
35086     0.319930     0.301316     0.437912    0.451406  
...            ...          ...          ...         ...  
7732   2016.603579   453.939569   439.516482  348.767036  
15055     0.000000   586.008513   510.832806  387.652260  
27659   583.651647     0.000000  1174.672068  639.223308  
30945   663.419809  1531.709856     0.000000  799.351985  
16080   613.424445  1015.597378   973.973547    0.000000  

[123 rows x 123 columns]

### Visualize histogram of flows

In [126]:
flow_matrix_pd.values

array([[0.00000000e+00, 5.31484493e+03, 3.40859183e+02, ...,
        3.51489294e-01, 5.11426382e-01, 5.27720150e-01],
       [4.14131430e+03, 0.00000000e+00, 2.01302410e+03, ...,
        1.01880112e+00, 1.48195395e+00, 1.52878275e+00],
       [1.38312439e+02, 1.04830491e+03, 0.00000000e+00, ...,
        9.11197264e-02, 1.32506307e-01, 1.36660238e-01],
       ...,
       [7.83677168e-02, 2.91519030e-01, 5.00669642e-02, ...,
        0.00000000e+00, 1.17467207e+03, 6.39223308e+02],
       [1.48685318e-01, 5.52932441e-01, 9.49369481e-02, ...,
        1.53170986e+03, 0.00000000e+00, 7.99351985e+02],
       [1.86938063e-01, 6.95011900e-01, 1.19302624e-01, ...,
        1.01559738e+03, 9.73973547e+02, 0.00000000e+00]])

In [127]:
flow_matrix_flattened = flow_matrix_pd.values.flatten()

In [128]:
flow_matrix_flattened

array([   0.        , 5314.84492832,  340.85918287, ..., 1015.59737795,
        973.97354678,    0.        ])

In [129]:
type(flow_matrix_flattened)

numpy.ndarray

In [130]:
flow_matrix_flattened.shape

(15129,)

In [131]:
#import matplotlib.pyplot as plt

In [132]:
#plt.rcParams['figure.figsize'] = [10, 5]

In [133]:
#n, bins, patches = plt.hist(flow_matrix_flattened, bins='auto', range=[0, 1000])

## For the base case compute the total cost flow matrix sum

In [134]:
cost_flow_matrix = OD_matrix * flow_matrix_pd

In [135]:
cost_flow_matrix

31313         4935          8705          6433          35086   
31313  0.000000e+00  4.045648e+07  4.330973e+06  3.354181e+07  5.363757e+06  \
4935   3.152360e+07  0.000000e+00  1.190125e+07  9.217086e+07  1.473928e+07   
8705   1.757404e+06  6.197710e+06  0.000000e+00  7.850478e+06  1.255390e+06   
6433   1.747196e+07  6.161708e+07  1.007778e+07  0.000000e+00  1.775748e+07   
35086  2.109007e+06  7.437680e+06  1.216470e+06  1.340402e+07  0.000000e+00   
...             ...           ...           ...           ...           ...   
7732   1.134187e+04  3.999856e+04  6.541964e+03  7.208450e+04  2.025497e+04   
15055  1.102969e+04  3.889759e+04  6.361895e+03  7.010036e+04  1.969745e+04   
27659  1.024816e+04  3.614145e+04  5.911115e+03  6.513331e+04  1.830176e+04   
30945  1.954689e+04  6.893460e+04  1.127460e+04  1.242324e+05  3.490797e+04   
16080  2.469002e+04  8.707248e+04  1.424114e+04  1.569201e+05  4.409285e+04   

              22045         12557         28219         11728         27665   
31313  3.288476e+06  7.319875e+06  2.409852e+06  3.505548e+06  2.851880e+07  \
4935   9.036533e+06  2.011457e+07  6.622127e+06  9.789038e+06  8.087597e+07   
8705   7.696695e+05  1.713221e+06  5.640271e+05  8.204754e+05  4.438725e+06   
6433   1.088733e+07  2.423348e+07  7.978156e+06  1.160561e+07  4.412941e+07   
35086  1.316441e+06  5.139955e+06  1.820502e+06  1.450732e+06  5.326777e+06   
...             ...           ...           ...           ...           ...   
7732   7.079595e+03  3.130759e+04  3.472365e+04  8.223408e+03  3.868099e+04   
15055  6.884727e+03  3.044584e+04  3.376787e+04  7.997057e+03  3.761628e+04   
27659  6.396902e+03  2.828856e+04  3.137521e+04  7.430416e+03  3.495094e+04   
30945  1.220117e+04  5.395635e+04  5.984367e+04  1.417245e+04  6.666386e+04   
16080  1.541150e+04  6.815319e+04  7.558957e+04  1.790146e+04  8.420427e+04   

       ...         1962           26726         6385          7971    
31313  ...  2.129833e+05   78257.441707  1.728456e+05  1.132905e+05  \
4935   ...  5.852652e+05  215046.692577  4.749693e+05  3.113153e+05   
8705   ...  4.984886e+04   18316.193691  4.045461e+04  2.651569e+04   
6433   ...  7.051115e+05  259082.341052  5.722299e+05  3.750642e+05   
35086  ...  1.495551e+05   54951.721092  1.213708e+05  7.955162e+04   
...    ...           ...            ...           ...           ...   
7732   ...  1.163308e+06  427439.453446  9.509474e+05  6.232919e+05   
15055  ...  1.131287e+06  415674.083937  9.247723e+05  6.061356e+05   
27659  ...  1.051129e+06  386221.000913  8.592465e+05  5.631872e+05   
30945  ...  2.004876e+06  736660.759305  1.638889e+06  1.074198e+06   
16080  ...  2.532393e+06  930488.868829  2.070108e+06  1.356838e+06   

               20108         7732          15055         27659         30945   
31313   48243.239759  4.770758e+04  4.927060e+04  4.596434e+04  6.723459e+04  \
4935   132569.490173  1.310975e+05  1.353926e+05  1.263072e+05  1.847566e+05   
8705    11291.354591  1.116598e+04  1.153181e+04  1.075798e+04  1.573629e+04   
6433   159716.075865  1.579427e+05  1.631173e+05  1.521714e+05  2.225896e+05   
35086   33875.999496  3.349986e+04  3.459740e+04  3.227577e+04  4.721157e+04   
...              ...           ...           ...           ...           ...   
7732   265420.548857  0.000000e+00  7.155513e+05  6.173487e+05  9.030303e+05   
15055  258114.787053  6.737808e+05  0.000000e+00  6.003560e+05  8.781741e+05   
27659  239825.755943  5.789728e+05  5.979414e+05  0.000000e+00  8.159501e+05   
30945  457432.980227  1.104307e+06  1.140487e+06  1.063955e+06  0.000000e+00   
16080  577791.460940  1.393971e+06  1.439641e+06  1.343035e+06  1.964533e+06   

              16080  
31313  6.969912e+04  
4935   1.915290e+05  
8705   1.631312e+04  
6433   2.307488e+05  
35086  4.894214e+04  
...             ...  
7732   9.355289e+05  
15055  9.097783e+05  
27659  8.453148e+05  
30945  1.612316e+06  
16080  0.000000e+00  

[123 rows x 123 columns]

In [136]:
flow_matrix_pd

31313        4935         8705         6433         35086   
31313     0.000000  5314.844928   340.859183  1940.539228   209.911399  \
4935   4141.314302     0.000000  2013.024101  8785.819342   785.736174   
8705    138.312439  1048.304911     0.000000  1714.549354    97.722843   
6433   1010.828596  5873.402547  2200.993922     0.000000  2147.565201   
35086    82.536275   396.495253    94.693178  1621.063788     0.000000   
...            ...          ...          ...          ...          ...   
7732      0.085839     0.319130     0.054779     0.627660     0.186723   
15055     0.083688     0.311179     0.053421     0.612172     0.182147   
27659     0.078368     0.291519     0.050067     0.573931     0.170859   
30945     0.148685     0.552932     0.094937     1.088030     0.323790   
16080     0.186938     0.695012     0.119303     1.366994     0.406680   

             22045        12557       28219        11728        27665  ...   
31313   154.409609   279.167846   36.540215   137.867188  1254.707400  ...  \
4935    623.072791  1035.423760  111.942019   537.389997  5349.836022  ...   
8705     89.589709   126.771029   10.593126    64.497973   215.284228  ...   
6433   2713.419466  2711.738457  163.934088  1425.196180  1751.395226  ...   
35086   107.590908  2003.065974   45.063937    93.577415   159.177362  ...   
...            ...          ...         ...          ...          ...  ...   
7732      0.059586     0.295606    0.304329     0.068123     0.292499  ...   
15055     0.058110     0.288383    0.296825     0.066433     0.285171  ...   
27659     0.054463     0.270575    0.278299     0.062255     0.267039  ...   
30945     0.103270     0.512676    0.527565     0.118056     0.506649  ...   
16080     0.129771     0.643832    0.662805     0.148363     0.636999  ...   

           1962       26726       6385       7971       20108        7732    
31313   1.585564   0.577321    1.364333   0.881402   0.353855     0.361065  \
4935    4.589143   1.670150    3.961549   2.557204   1.023369     1.045966   
8705    0.409872   0.149098    0.354919   0.228922   0.091332     0.093499   
6433    6.024396   2.190620    5.230384   3.371345   1.341562     1.375252   
35086   1.351334   0.491085    1.177963   0.758500   0.300634     0.308823   
...          ...        ...         ...        ...        ...          ...   
7732   41.132930  14.485571   46.488308  27.948697   8.817089     0.000000   
15055  40.480949  14.248857   45.962547  27.594530   8.671035  1898.883849   
27659  39.043942  13.721097   44.996987  26.893603   8.343800   425.721612   
30945  72.597553  25.540731   82.812867  49.648819  15.539068   537.480469   
16080  89.714103  31.591625  101.469263  60.989728  19.228516   519.675277   

             15055        27659        30945       16080  
31313     0.373844     0.351489     0.511426    0.527720  
4935      1.083134     1.018801     1.481954    1.528783  
8705      0.096834     0.091120     0.132506    0.136660  
6433      1.424470     1.340878     1.949445    2.010146  
35086     0.319930     0.301316     0.437912    0.451406  
...            ...          ...          ...         ...  
7732   2016.603579   453.939569   439.516482  348.767036  
15055     0.000000   586.008513   510.832806  387.652260  
27659   583.651647     0.000000  1174.672068  639.223308  
30945   663.419809  1531.709856     0.000000  799.351985  
16080   613.424445  1015.597378   973.973547    0.000000  

[123 rows x 123 columns]

In [137]:
flow_matrix_pd.sum(axis=0)

31313     8360.501756
4935     27184.757986
8705      6597.293100
6433     37096.620454
35086    10418.599529
             ...     
7732      4990.188473
15055     5568.028482
27659     5257.492171
30945     5448.147000
16080     4531.555266
Length: 123, dtype: float64

In [138]:
# sum each row
flow_matrix_pd.sum(axis=1)

31313    14214.519489
4935     38589.649943
8705      5026.444239
6433     46434.021615
35086    10209.088599
             ...     
7732      5501.743691
15055     5609.059167
27659     5030.252792
30945     7557.503249
16080     8021.070721
Length: 123, dtype: float64

In [139]:
origins['Pop'].to_list()

[14214.519489352126,
 38589.649942575954,
 5026.44423872605,
 46434.0216147434,
 10209.088599480689,
 5313.074770569801,
 14295.21543551609,
 21733.1979159303,
 6640.108931705356,
 48689.689116044436,
 7079.620935236104,
 5697.381296921521,
 19114.45952611603,
 16233.29442803841,
 5746.3903532624245,
 7869.3957715900615,
 78871.45581687219,
 8713.955182519741,
 5018.3257643748075,
 5204.280054014176,
 8246.580115709454,
 6968.8557211030275,
 9165.328496575356,
 5540.089683309197,
 5157.728648264892,
 7788.110119457357,
 49034.19717816543,
 32732.95508956164,
 5250.598972450942,
 7495.581114942208,
 14482.796854425222,
 7352.569241038989,
 9394.842671385035,
 10178.287221826613,
 6531.459656964056,
 8203.841480255127,
 13205.387299675494,
 6136.646688371897,
 7396.475869633257,
 23886.154249701183,
 8385.142450579617,
 15798.19849751098,
 15179.305181124248,
 9985.448286615312,
 14746.84131473303,
 5539.216975815594,
 9644.637944828719,
 34960.6294361233,
 21566.721199831925,
 20509.724

In [140]:
cost_flow_matrix.sum().sum()

29209756554.760643

In [141]:
# hours of travel time
base_total_tt_hours = cost_flow_matrix.sum().sum()/60/60

In [142]:
base_total_tt_hours

8113821.26521129

# Disruption

In [143]:
import collections
shortest_paths_per_rd_dict = collections.defaultdict(list)

In [144]:
shortest_paths_per_rd_dict

defaultdict(list, {})

## Build index of shortest paths that pass through road segments

In [145]:
%%time
for origin1 in originNodes:
    for origin2 in originNodes:
        
        #print(origin1)
        #print(origin2)
        if origin1 != origin2:
            route = nx.dijkstra_path(G_w_time, origin1, origin2, weight = 'time')
            #print(route)
            # parse through shortest route segments
            for idx in range(0, len(route) - 1):
                # if flow is greater than 100
                if flow_matrix_pd[origin1][origin2] > 100:
                    # add origin and destination to shortest_paths_per_rd_dict if does not exist
                    shortest_paths_per_rd_dict[route[idx], route[idx+1]].append((origin1, origin2))

CPU times: user 57.4 s, sys: 219 ms, total: 57.6 s
Wall time: 57.6 s


In [146]:
shortest_paths_per_rd_dict

defaultdict(list,
            {(31313, 7805): [(31313, 4935),
              (31313, 8705),
              (31313, 6433),
              (31313, 12557),
              (31313, 27665),
              (31313, 16978),
              (31313, 11318)],
             (7805, 11264): [(31313, 4935), (31313, 27665)],
             (11264, 17417): [(31313, 4935), (31313, 27665)],
             (17417, 259): [(31313, 4935), (31313, 27665)],
             (259, 3689): [(31313, 4935), (31313, 27665)],
             (3689, 4935): [(31313, 4935), (31313, 27665)],
             (7805, 30211): [(31313, 8705),
              (31313, 6433),
              (31313, 12557),
              (31313, 16978),
              (31313, 11318)],
             (30211, 20672): [(31313, 8705),
              (31313, 6433),
              (31313, 12557),
              (31313, 16978),
              (31313, 11318)],
             (20672, 28646): [(31313, 8705),
              (31313, 6433),
              (31313, 12557),
              (31313, 16

In [147]:
# road disruption list are the keys of shortest_paths_per_rd_dict

In [148]:
shortest_paths_per_rd_dict.keys()

dict_keys([(31313, 7805), (7805, 11264), (11264, 17417), (17417, 259), (259, 3689), (3689, 4935), (7805, 30211), (30211, 20672), (20672, 28646), (28646, 47), (47, 20421), (20421, 15343), (15343, 8894), (8894, 21614), (21614, 8705), (8705, 12518), (12518, 3561), (3561, 14217), (14217, 11262), (11262, 27801), (27801, 35797), (35797, 16612), (16612, 27597), (27597, 20390), (20390, 2655), (2655, 5091), (5091, 6980), (6980, 6433), (2655, 11961), (11961, 30694), (30694, 24482), (24482, 26991), (26991, 20203), (20203, 35868), (35868, 21942), (21942, 23535), (23535, 19491), (19491, 22665), (22665, 15595), (15595, 4286), (4286, 12557), (4935, 21700), (21700, 2013), (2013, 17469), (17469, 30969), (30969, 20970), (20970, 22354), (22354, 32821), (32821, 9136), (9136, 3403), (3403, 33006), (33006, 31162), (31162, 30272), (30272, 6750), (6750, 32250), (32250, 19799), (19799, 27665), (12557, 36212), (36212, 16899), (16899, 4742), (4742, 27488), (27488, 29523), (29523, 8783), (8783, 17628), (17628, 24

In [149]:
# number of road segments that have flow
len(shortest_paths_per_rd_dict.keys())

1975

In [150]:
for key in shortest_paths_per_rd_dict:
    print(key)

(31313, 7805)
(7805, 11264)
(11264, 17417)
(17417, 259)
(259, 3689)
(3689, 4935)
(7805, 30211)
(30211, 20672)
(20672, 28646)
(28646, 47)
(47, 20421)
(20421, 15343)
(15343, 8894)
(8894, 21614)
(21614, 8705)
(8705, 12518)
(12518, 3561)
(3561, 14217)
(14217, 11262)
(11262, 27801)
(27801, 35797)
(35797, 16612)
(16612, 27597)
(27597, 20390)
(20390, 2655)
(2655, 5091)
(5091, 6980)
(6980, 6433)
(2655, 11961)
(11961, 30694)
(30694, 24482)
(24482, 26991)
(26991, 20203)
(20203, 35868)
(35868, 21942)
(21942, 23535)
(23535, 19491)
(19491, 22665)
(22665, 15595)
(15595, 4286)
(4286, 12557)
(4935, 21700)
(21700, 2013)
(2013, 17469)
(17469, 30969)
(30969, 20970)
(20970, 22354)
(22354, 32821)
(32821, 9136)
(9136, 3403)
(3403, 33006)
(33006, 31162)
(31162, 30272)
(30272, 6750)
(6750, 32250)
(32250, 19799)
(19799, 27665)
(12557, 36212)
(36212, 16899)
(16899, 4742)
(4742, 27488)
(27488, 29523)
(29523, 8783)
(8783, 17628)
(17628, 2434)
(2434, 16943)
(16943, 32142)
(32142, 14762)
(14762, 13758)
(13758, 1697

In [151]:
# testing, label the edges where flow occurs

nx.set_edge_attributes(G_w_time, 0, 'flow')

for key in shortest_paths_per_rd_dict:
    #shortest_path_dict[key[0],key[1],0]={'shrt_pth':1}
    for edge in G_w_time[key[0]][key[1]]:
        print(edge)
        print(G_w_time[key[0]][key[1]][edge])
        G_w_time[key[0]][key[1]][edge]['flow'] = 1

edge_12765
{'Wkt': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'id': 12765, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253280287', 'length': 57622.05800185242, 'Type': 'legitimate', 'geometry': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'time': 6914.6469602222905, 'mode': 'drive', 'flow': 0, 'flow_amount': 13077.077437568158}
0
{'Wkt': <LINESTRING (101.408 21.015, 101.408 21.014)>, 'id': 12804, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253281689', 'key': 'edge_12804', 'length': 20.105865645019616, 'Type': 'legitimate', 'time': 2.412703877402354, 'mode': 'drive', 'flow': 0, 'flow_amount': 13077.077437568158}
0
{'Wkt': <LINESTRING (101.408 21.014, 101.408 21.014, 101.408 21.014)>, 'id': 12810, 'infra_type': 'primary', 'one_way': None, 'osm_id': '253281690', 'key': 'edge_12810', 'length': 6.832925886488708, 'Type': 'legitimate', 'time': 0.6149633297839837, 'mode': 'drive', 'flow': 0, 'flo

In [152]:
# for testing
# G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_w_time, geometry_tag = 'geometry')
# G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns = ['Wkt'])
# G_adv_w_time_gdf.to_file("flow_G_adv_w_time_criticality5_lambda.shp")

### for testing compute flow amounts in baseline scenario

In [153]:
shortest_paths_flows = collections.defaultdict(list)

In [154]:
%%time
for origin1 in originNodes:
    for origin2 in originNodes:
        
        #print(origin1)
        #print(origin2)
        if origin1 != origin2:
            route = nx.dijkstra_path(G_w_time, origin1, origin2, weight = 'time')
            #print(route)
            # parse through shortest route segments
            for idx in range(0, len(route) - 1):
                # if flow is greater than 100
                if flow_matrix_pd[origin1][origin2] > 100:
                    # add flows
                    shortest_paths_flows[route[idx], route[idx+1]].append(flow_matrix_pd[origin1][origin2])

CPU times: user 59.1 s, sys: 323 ms, total: 59.4 s
Wall time: 59.4 s


In [155]:
shortest_paths_flows

defaultdict(list,
            {(31313, 7805): [4141.3143024425535,
              138.312438845829,
              1010.8285962240634,
              103.3507983420301,
              1394.4706117184016,
              380.95619359763367,
              245.25138060746653],
             (7805, 11264): [4141.3143024425535, 1394.4706117184016],
             (11264, 17417): [4141.3143024425535, 1394.4706117184016],
             (17417, 259): [4141.3143024425535, 1394.4706117184016],
             (259, 3689): [4141.3143024425535, 1394.4706117184016],
             (3689, 4935): [4141.3143024425535, 1394.4706117184016],
             (7805, 30211): [138.312438845829,
              1010.8285962240634,
              103.3507983420301,
              380.95619359763367,
              245.25138060746653],
             (30211, 20672): [138.312438845829,
              1010.8285962240634,
              103.3507983420301,
              380.95619359763367,
              245.25138060746653],
             (206

In [156]:
shortest_paths_flows[(6016, 8810)]

[117.32801446711358,
 483.13060339809437,
 197.78339182071878,
 577.148668986697,
 226.8968063679081,
 209.04911929356282,
 156.81286422096383,
 188.26894842490933,
 110.65804816210633,
 345.03457697907766,
 118.50160428210867,
 661.8399096811464,
 221.08186060340765,
 323.2725988067713,
 107.07858902485597,
 119.7777630406065,
 1631.7562278934458,
 514.9361572187452,
 126.50176103194168,
 180.9847071561347,
 306.6117820603429,
 115.5984893217669,
 1128.1315884741966,
 349.8570632007593,
 115.41863827575693,
 295.7063935764715,
 111.13585436767566,
 204.86409173194025,
 109.09548496708791,
 2983.6406640531955,
 157.20387609541012,
 897.402408511866,
 115.78151293716599,
 213.6525753644902,
 504.4429276657058,
 186.63561757103048,
 216.7494347937422,
 136.55251792495235,
 224.872373605274,
 234.0510870964065,
 406.17271876648397,
 147.70541953352986,
 1464.431789743666,
 332.2128832755298,
 227.13978639047326,
 181.60804862985125,
 217.65721486096294,
 318.7851470929908,
 114.5822814156

In [157]:
sum(shortest_paths_flows[(6016, 8810)])

54692.484634549386

In [158]:
for key in shortest_paths_flows:
    print(shortest_paths_flows[key])

[4141.3143024425535, 138.312438845829, 1010.8285962240634, 103.3507983420301, 1394.4706117184016, 380.95619359763367, 245.25138060746653]
[4141.3143024425535, 1394.4706117184016]
[4141.3143024425535, 1394.4706117184016]
[4141.3143024425535, 1394.4706117184016]
[4141.3143024425535, 1394.4706117184016]
[4141.3143024425535, 1394.4706117184016]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.95619359763367, 245.25138060746653]
[138.312438845829, 1010.8285962240634, 103.3507983420301, 380.9561935

In [159]:
nx.set_edge_attributes(G_w_time, 0, 'flow_amount')

for key in shortest_paths_flows:
    #shortest_path_dict[key[0],key[1],0]={'shrt_pth':1}
    for edge in G_w_time[key[0]][key[1]]:
        print(edge)
        G_w_time[key[0]][key[1]][edge]['flow_amount'] = sum(shortest_paths_flows[key])
        print(G_w_time[key[0]][key[1]][edge])

edge_12765
{'Wkt': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'id': 12765, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253280287', 'length': 57622.05800185242, 'Type': 'legitimate', 'geometry': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'time': 6914.6469602222905, 'mode': 'drive', 'flow': 1, 'flow_amount': 7414.484321777978}
0
{'Wkt': <LINESTRING (101.408 21.015, 101.408 21.014)>, 'id': 12804, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253281689', 'key': 'edge_12804', 'length': 20.105865645019616, 'Type': 'legitimate', 'time': 2.412703877402354, 'mode': 'drive', 'flow': 1, 'flow_amount': 5535.784914160955}
0
{'Wkt': <LINESTRING (101.408 21.014, 101.408 21.014, 101.408 21.014)>, 'id': 12810, 'infra_type': 'primary', 'one_way': None, 'osm_id': '253281690', 'key': 'edge_12810', 'length': 6.832925886488708, 'Type': 'legitimate', 'time': 0.6149633297839837, 'mode': 'drive', 'flow': 1, 'flow_

In [160]:
# for testing
G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_w_time, geometry_tag = 'geometry')
G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns = ['Wkt'])
G_adv_w_time_gdf.to_file("flow_G_adv_w_time_criticality5_300m_lambda.shp")

/var/folders/gr/04wfn6914nn08mfvwlf0_j2h0000gn/T/ipykernel_24562/1332389846.py:4: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  G_adv_w_time_gdf.to_file("flow_G_adv_w_time_criticality5_300m_lambda.shp")


In [161]:
# however only a subset of shortest paths flow through the road that gets disrupted each iteration, 
# so the real-word number of calculations is lower

# count how many shortest paths need to be re-computed for each road disrupted
count = 0
for key in shortest_paths_per_rd_dict.keys():
    for ODpair in shortest_paths_per_rd_dict[key]:
        count += 1
count

63463

# To-do: I think ideally the flows could be recalculated as well each time a road is disrupted....

# Computing the total cost flow matrix sum for each disrupted road is taking too long. Reduced processing time from 5 hours to under a half hour.

In [162]:
%%time
count = 0
result_dict = {}
#LIMIT = 100000
# for each road that has at least one shortest path flowing through it
#for key in islice(shortest_paths_per_rd_dict.keys(), LIMIT):
with open('datagathered5','w') as f:
    
    for key in shortest_paths_per_rd_dict.keys():
        print(f'key is {key}')

        #make a deep copy of OD_matrix for each road disruption
        OD_matrix_deep_copy = OD_matrix.copy()
        #convert to pandas dataframe with headers
        OD_matrix_deep_copy_df = pd.DataFrame(OD_matrix_deep_copy, columns = originNodes, index = originNodes)

        G_w_time_copy = G_w_time.copy()
        
        #disrupt network
        G_w_time_copy.remove_edge(key[0],key[1])

        # for each shortest path that flows through the road
        for ODpair in shortest_paths_per_rd_dict[key]:
            count += 1
            if count % 500 == 0:
                print(f'current count is {count}')
            #print(ODpair)
            # only re-calculate OD pairs that are affected by the disrupted road
            #OD_matrix_deep_copy = update_OD_matrix(OD_matrix_deep_copy_df, nx.shortest_path(G_w_time, ODpair[0], ODpair[1],weight='time'),ODpair)
            try:
                #print(f'shortest path before: {OD_matrix_deep_copy_df[ODpair[0]][ODpair[1]]}')
                OD_matrix_deep_copy_df[ODpair[0]][ODpair[1]] = nx.shortest_path_length(G_w_time_copy, ODpair[0], ODpair[1], weight='time')
                #print(f'shortest path after: {OD_matrix_deep_copy_df[ODpair[0]][ODpair[1]]}')
            except Exception as e:
                #print("Oops!", sys.exc_info()[0], "occurred.")
                #print(e)
                #print("Next entry.")
                #print()
                continue

        # re-calculate the total travel times
        cost_flow_matrix_times_tt = flow_matrix_pd * OD_matrix_deep_copy_df
        # in total hours
        result_dict[key] = cost_flow_matrix_times_tt.to_numpy().sum()/60/60

        f.write(f'{key}: {result_dict[key]};\n')

key is (31313, 7805)
key is (7805, 11264)
key is (11264, 17417)
key is (17417, 259)
key is (259, 3689)
key is (3689, 4935)
key is (7805, 30211)
key is (30211, 20672)
key is (20672, 28646)
key is (28646, 47)
key is (47, 20421)
key is (20421, 15343)
key is (15343, 8894)
key is (8894, 21614)
key is (21614, 8705)
key is (8705, 12518)
key is (12518, 3561)
key is (3561, 14217)
key is (14217, 11262)
key is (11262, 27801)
key is (27801, 35797)
key is (35797, 16612)
key is (16612, 27597)
key is (27597, 20390)
key is (20390, 2655)
key is (2655, 5091)
key is (5091, 6980)
key is (6980, 6433)
key is (2655, 11961)
key is (11961, 30694)
key is (30694, 24482)
key is (24482, 26991)
key is (26991, 20203)
key is (20203, 35868)
key is (35868, 21942)
key is (21942, 23535)
current count is 500
key is (23535, 19491)
key is (19491, 22665)
key is (22665, 15595)
key is (15595, 4286)
key is (4286, 12557)
key is (4935, 21700)
key is (21700, 2013)
key is (2013, 17469)
key is (17469, 30969)
key is (30969, 20970)
ke

key is (35086, 4286)
key is (4286, 15595)
key is (15595, 22665)
key is (22665, 19491)
key is (19491, 23535)
key is (23535, 21942)
key is (21942, 35868)
key is (35868, 20203)
current count is 15000
key is (20203, 26991)
key is (26991, 24482)
key is (24482, 30694)
key is (30694, 11961)
key is (11961, 2655)
key is (21942, 23253)
key is (23253, 11082)
key is (11082, 6625)
key is (6625, 25697)
key is (25697, 29172)
key is (29172, 13388)
key is (13388, 6433)
current count is 15500
key is (15595, 35793)
key is (35793, 3428)
key is (22045, 18302)
key is (18302, 21105)
key is (21105, 25697)
key is (29172, 24482)
key is (12557, 4286)
key is (28219, 28382)
key is (28382, 10500)
key is (10500, 19365)
key is (19365, 1204)
key is (1204, 18888)
key is (18888, 25594)
key is (25594, 32334)
key is (32334, 25893)
key is (25893, 23587)
key is (23587, 17854)
key is (17854, 2454)
key is (2454, 16629)
key is (16629, 35086)
key is (10500, 5606)
key is (17854, 27488)
key is (25893, 16049)
key is (16049, 35600)

key is (29847, 19082)
key is (19082, 2662)
key is (32197, 862)
key is (862, 12882)
key is (12882, 35376)
key is (17098, 35376)
key is (35376, 29847)
key is (35376, 12882)
current count is 24500
key is (12882, 862)
key is (862, 32197)
key is (409, 17787)
key is (17787, 17098)
key is (1569, 17787)
key is (5761, 15475)
key is (15475, 18240)
key is (18240, 6815)
key is (6815, 19665)
key is (19665, 1483)
key is (1483, 22348)
key is (22348, 30865)
key is (30865, 538)
key is (538, 20707)
key is (20707, 18221)
current count is 25000
key is (5761, 4544)
key is (4544, 20353)
key is (20353, 18797)
key is (11161, 18777)
key is (18777, 6945)
key is (6945, 1729)
key is (1729, 2167)
key is (2167, 10864)
key is (10864, 35461)
key is (35461, 8593)
key is (8593, 36326)
key is (36326, 26499)
key is (26499, 21025)
key is (21025, 19719)
key is (19719, 29084)
key is (29084, 10064)
key is (10064, 30364)
key is (11161, 30998)
key is (30998, 11442)
key is (11442, 10291)
key is (10291, 23394)
key is (23394, 129

key is (16121, 36097)
key is (36097, 3067)
key is (3067, 4856)
key is (4856, 3452)
key is (3452, 14338)
key is (14338, 29778)
key is (29778, 14479)
key is (14479, 1176)
key is (1176, 26227)
key is (26227, 23380)
key is (23380, 14026)
key is (14026, 10841)
key is (26800, 23634)
key is (23634, 18363)
key is (18363, 24706)
key is (24706, 17597)
key is (17597, 19242)
key is (19242, 2231)
current count is 39000
key is (2231, 33933)
key is (33933, 14413)
key is (14413, 7651)
key is (24648, 4141)
key is (4141, 16162)
key is (16162, 29430)
key is (29430, 36069)
key is (36069, 16849)
key is (16849, 14657)
key is (14657, 9007)
key is (9007, 30121)
key is (30121, 18192)
key is (18192, 25916)
key is (25916, 9783)
key is (9783, 33448)
key is (33448, 1396)
key is (1396, 25970)
key is (25970, 3287)
key is (3287, 12880)
key is (12880, 1430)
key is (1430, 32472)
key is (32472, 12838)
key is (12838, 2223)
key is (2223, 21119)
key is (21119, 34047)
key is (34047, 13385)
key is (13385, 29980)
key is (2998

key is (25557, 13844)
key is (13844, 1606)
key is (1606, 18934)
key is (18934, 7339)
key is (7339, 32480)
key is (32480, 3693)
key is (3693, 3295)
current count is 47000
key is (3295, 12919)
key is (12919, 6385)
key is (6385, 7971)
key is (12698, 9066)
key is (9066, 14301)
key is (14301, 7914)
key is (7914, 2741)
key is (2741, 33719)
key is (33719, 25444)
key is (25444, 9667)
key is (9667, 33478)
key is (33478, 20108)
key is (13667, 28595)
key is (28595, 23207)
key is (23207, 11860)
current count is 47500
key is (11860, 3296)
key is (3296, 2606)
key is (2606, 27911)
key is (27911, 10612)
key is (10612, 4844)
key is (4844, 29630)
key is (29630, 2818)
key is (2818, 16080)
key is (12852, 16954)
key is (16954, 13806)
key is (11002, 35721)
key is (35721, 31570)
key is (31570, 18324)
key is (18324, 32857)
current count is 48000
key is (32857, 8810)
key is (8810, 6016)
key is (6016, 23925)
key is (23925, 32372)
key is (32372, 5483)
key is (5483, 34282)
current count is 48500
key is (32372, 27

current count is 59000
key is (36192, 27694)
key is (27694, 2866)
key is (36192, 22398)
key is (12736, 16094)
key is (16094, 11376)
key is (11376, 16363)
key is (18742, 25414)
key is (25414, 4065)
key is (25384, 24394)
key is (32504, 8359)
key is (8359, 4303)
key is (13667, 20953)
key is (20953, 22429)
key is (22429, 16633)
current count is 59500
key is (16633, 1623)
key is (1623, 9448)
key is (9448, 7406)
key is (7406, 8326)
key is (8326, 13184)
key is (13184, 21724)
current count is 60000
key is (21724, 10952)
key is (10952, 30931)
key is (30931, 36339)
key is (36339, 25655)
key is (25655, 12324)
key is (12324, 1153)
current count is 60500
key is (1153, 8238)
key is (8238, 32504)
key is (32504, 25384)
key is (25384, 31816)
key is (31816, 26524)
current count is 61000
key is (26524, 25414)
key is (8905, 2029)
key is (24305, 7828)
key is (7828, 736)
key is (736, 34418)
key is (34418, 26897)
key is (26897, 19058)
key is (736, 19165)
key is (29626, 27430)
key is (27430, 26524)
key is (25

In [163]:
result_dict

{(31313, 7805): 8113821.265211287,
 (7805, 11264): 8113822.404436997,
 (11264, 17417): 8113822.645499196,
 (17417, 259): 8113822.645499196,
 (259, 3689): 8115055.1115374975,
 (3689, 4935): 8113821.265211287,
 (7805, 30211): 8113821.872823481,
 (30211, 20672): 8113822.547938408,
 (20672, 28646): 8113821.943717312,
 (28646, 47): 8114248.176693413,
 (47, 20421): 8113821.711515215,
 (20421, 15343): 8113822.02122929,
 (15343, 8894): 8113822.02122929,
 (8894, 21614): 8140936.157373041,
 (21614, 8705): 8140936.157373041,
 (8705, 12518): 8185939.636270362,
 (12518, 3561): 8185939.636270362,
 (3561, 14217): 8185939.636270362,
 (14217, 11262): 8185939.636270362,
 (11262, 27801): 8185939.636270362,
 (27801, 35797): 8116913.1875180015,
 (35797, 16612): 8114393.372469031,
 (16612, 27597): 8113886.32440933,
 (27597, 20390): 8113901.068526494,
 (20390, 2655): 8116913.1875180015,
 (2655, 5091): 8113822.539194673,
 (5091, 6980): 8113824.1507379515,
 (6980, 6433): 8113827.590833564,
 (2655, 11961): 8113

In [164]:
base_total_tt_hours

8113821.26521129

In [165]:
#diff between base case?
result_dict_diff = {}
for key in result_dict:
    print(key)
    result_dict_diff[key] = result_dict[key] - base_total_tt_hours
    

(31313, 7805)
(7805, 11264)
(11264, 17417)
(17417, 259)
(259, 3689)
(3689, 4935)
(7805, 30211)
(30211, 20672)
(20672, 28646)
(28646, 47)
(47, 20421)
(20421, 15343)
(15343, 8894)
(8894, 21614)
(21614, 8705)
(8705, 12518)
(12518, 3561)
(3561, 14217)
(14217, 11262)
(11262, 27801)
(27801, 35797)
(35797, 16612)
(16612, 27597)
(27597, 20390)
(20390, 2655)
(2655, 5091)
(5091, 6980)
(6980, 6433)
(2655, 11961)
(11961, 30694)
(30694, 24482)
(24482, 26991)
(26991, 20203)
(20203, 35868)
(35868, 21942)
(21942, 23535)
(23535, 19491)
(19491, 22665)
(22665, 15595)
(15595, 4286)
(4286, 12557)
(4935, 21700)
(21700, 2013)
(2013, 17469)
(17469, 30969)
(30969, 20970)
(20970, 22354)
(22354, 32821)
(32821, 9136)
(9136, 3403)
(3403, 33006)
(33006, 31162)
(31162, 30272)
(30272, 6750)
(6750, 32250)
(32250, 19799)
(19799, 27665)
(12557, 36212)
(36212, 16899)
(16899, 4742)
(4742, 27488)
(27488, 29523)
(29523, 8783)
(8783, 17628)
(17628, 2434)
(2434, 16943)
(16943, 32142)
(32142, 14762)
(14762, 13758)
(13758, 1697

In [166]:
result_dict_diff

{(31313, 7805): -2.7939677238464355e-09,
 (7805, 11264): 1.1392257073894143,
 (11264, 17417): 1.3802879061549902,
 (17417, 259): 1.3802879061549902,
 (259, 3689): 1233.846326207742,
 (3689, 4935): -2.7939677238464355e-09,
 (7805, 30211): 0.6076121916994452,
 (30211, 20672): 1.2827271185815334,
 (20672, 28646): 0.6785060223191977,
 (28646, 47): 426.91148212365806,
 (47, 20421): 0.4463039254769683,
 (20421, 15343): 0.7560180006548762,
 (15343, 8894): 0.7560180006548762,
 (8894, 21614): 27114.892161751166,
 (21614, 8705): 27114.892161751166,
 (8705, 12518): 72118.3710590722,
 (12518, 3561): 72118.3710590722,
 (3561, 14217): 72118.3710590722,
 (14217, 11262): 72118.3710590722,
 (11262, 27801): 72118.3710590722,
 (27801, 35797): 3091.9223067117855,
 (35797, 16612): 572.1072577415034,
 (16612, 27597): 65.05919804051518,
 (27597, 20390): 79.80331520456821,
 (20390, 2655): 3091.9223067117855,
 (2655, 5091): 1.27398338355124,
 (5091, 6980): 2.885526661761105,
 (6980, 6433): 6.325622274540365,
 

## Assign dictionary values to graph as a criticality attribute and save as shapefile

In [167]:
gn.example_edge(G_w_time)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 16.002568065588846, 'Type': 'legitimate', 'time': 1.440231125902996, 'mode': 'drive', 'flow': 0, 'flow_amount': 0})


In [168]:
#set baseline criticality of 0
nx.set_edge_attributes(G_w_time, 0, 'criticality')

In [169]:
gn.example_edge(G_w_time)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 16.002568065588846, 'Type': 'legitimate', 'time': 1.440231125902996, 'mode': 'drive', 'flow': 0, 'flow_amount': 0, 'criticality': 0})


In [170]:
for key in result_dict_diff:
    #shortest_path_dict[key[0],key[1],0]={'shrt_pth':1}
    for edge in G_w_time[key[0]][key[1]]:
        print(edge)
        print(G_w_time[key[0]][key[1]][edge])
        G_w_time[key[0]][key[1]][edge]['criticality'] = result_dict_diff[key]

edge_12765
{'Wkt': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'id': 12765, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253280287', 'length': 57622.05800185242, 'Type': 'legitimate', 'geometry': <LINESTRING (101.148 21.185, 101.149 21.183, 101.15 21.181, 101.154 21.175, ...>, 'time': 6914.6469602222905, 'mode': 'drive', 'flow': 1, 'flow_amount': 7414.484321777978, 'criticality': 0}
0
{'Wkt': <LINESTRING (101.408 21.015, 101.408 21.014)>, 'id': 12804, 'infra_type': 'secondary', 'one_way': None, 'osm_id': '253281689', 'key': 'edge_12804', 'length': 20.105865645019616, 'Type': 'legitimate', 'time': 2.412703877402354, 'mode': 'drive', 'flow': 1, 'flow_amount': 5535.784914160955, 'criticality': 0}
0
{'Wkt': <LINESTRING (101.408 21.014, 101.408 21.014, 101.408 21.014)>, 'id': 12810, 'infra_type': 'primary', 'one_way': None, 'osm_id': '253281690', 'key': 'edge_12810', 'length': 6.832925886488708, 'Type': 'legitimate', 'time': 0.6149633297839837

In [171]:
G_w_time.is_multigraph()

True

In [172]:
gn.example_edge(G_w_time,5)

(1, 31106, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9213, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'key': 'edge_9213', 'length': 16.002568065588846, 'Type': 'legitimate', 'time': 1.440231125902996, 'mode': 'drive', 'flow': 0, 'flow_amount': 0, 'criticality': 0})
(1, 35427, {'Wkt': <LINESTRING (102.727 18.023, 102.727 18.023)>, 'id': 9230, 'infra_type': 'primary_link', 'one_way': None, 'osm_id': '221460953', 'key': 'edge_9230', 'length': 12.132278961277224, 'Type': 'legitimate', 'time': 1.2478915503028003, 'mode': 'drive', 'flow': 0, 'flow_amount': 0, 'criticality': 0})
(1, 16050, {'Wkt': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>, 'id': 9214, 'infra_type': 'primary', 'one_way': None, 'osm_id': '221459014', 'length': 1518.4586030002702, 'Type': 'legitimate', 'geometry': <LINESTRING (102.727 18.023, 102.725 18.019, 102.724 18.017, 102.722 18.01)>, 'time': 136.66127427002434, 'mode': 'drive', 'flow': 0, 'flow_am

In [173]:
# for testing
G_adv_w_time_gdf = gn.edge_gdf_from_graph(G_w_time, geometry_tag='geometry')
G_adv_w_time_gdf = G_adv_w_time_gdf.drop(columns=['Wkt'])
G_adv_w_time_gdf.to_file("G_adv_w_time_criticality14_300m_lambda.shp")

/var/folders/gr/04wfn6914nn08mfvwlf0_j2h0000gn/T/ipykernel_24562/3556192325.py:4: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  G_adv_w_time_gdf.to_file("G_adv_w_time_criticality14_300m_lambda.shp")
